In [12]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

g_year = 108
g_season = 1
g_how_many_year = 3

In [13]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True)#, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'公司代號'] != u'公司代號']
    df = df[~df[u'公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [14]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',u'公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on=u'公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [15]:
df_net_income_sii = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'sii', 'NetIncome', '稅後純益率(%)(稅後純益)/(營業收入)', '營益分析彙總表')

df_net_income_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



稅後純益率(%)(稅後純益)/(營業收入)
year: 107
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 2


公司代號     公司名稱 NetIncome(%)_107Q2 NetIncome(%)_107Q1 NetIncome(%)_106Q4  \
0    1101       台泥              18.39              11.85              10.50   
1    1102       亞泥              19.95              14.57              10.27   
2    1103       嘉泥              44.12              33.99              46.64   
3    1104     環球水泥              17.64               0.20              31.54   
4    1108     幸福水泥              -0.48              -0.74              -3.00   
5    1109     信大水泥              13.96              16.05              13.21   
6    1110       東泥               7.00               3.72               3.40   
7    1201     味全公司              -0.58               3.27               5.03   
8    1203     味王公司              11.26              10.51              12.05   
9    1210     大成長城               3.73               5.40               3.49   
10   1213       大飲               0.69               1.13               0.31   
11   1215     卜蜂企業               4.02               5.44               7.44   
12   1216       統一               7.07               6.26              15.00   
13   1217      愛之味               0.42               3.90               3.50   
14   1218     泰山企業               5.61               4.40               4.13   
15   1219     福壽實業               1.03               1.56               0.51   
16   1220       台榮               5.51               5.89               3.56   
17   1225      福懋油               3.33               3.44               2.98   
18   1227       佳格               8.82              10.03               8.35   
19   1229     聯華實業              47.80              44.53              61.07   
20   1231     聯華食品               5.37               6.68               5.79   
21   1232      大統益               5.24               4.91               4.93   
22   1233       天仁               8.68               6.97               8.23   
23   1234       黑松               6.48               5.13               5.98   
24   1235       興泰             211.87             150.04             399.16   
25   1236     宏亞食品              -1.94               5.88               0.27   
26   1256  鮮活果汁-KY              13.58               9.32               9.84   
27   1262    綠悅-KY              -8.61              -1.83              12.16   
28   1301       台塑              24.89              21.94              23.89   
29   1303     南亞塑膠              17.71              16.14              17.63   
30   1304       台聚               5.50               5.56               4.66   
31   1305       華夏              12.81              14.08               9.11   
32   1307     三芳化工               3.68               4.33               9.14   
33   1308       亞聚               5.45               6.24               8.83   
34   1309     台達化工               3.54               3.92               2.53   
35   1310       台苯               8.84               9.66               6.67   
36   1312     國喬石化              14.98              15.74              14.76   
37   1313       聯成               1.93               3.18               4.63   
38   1314      中石化              12.25              11.62              18.26   
39   1315     達新工業              -1.47              -1.54               6.34   
40   1316       上曜              18.57              18.01              15.10   
41   1319       東陽               9.07               8.06               9.80   
42   1321       大洋              -1.38               3.34              -1.82   
43   1323       永裕               9.46               8.67               9.68   
44   1324     地球工業               0.19              -2.06               4.91   
45   1325       恒大               7.07               3.34               4.59   
46   1326       台化              15.38              14.48              16.75   
47   1337    再生-KY             -39.96             -39.92               3.97   
48   1338    廣華-KY               7.78               9.21               9.31   
49   1339       昭輝              17.38               7.2

In [ ]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_net_income_sii.columns # the column index
#idx = df_net_income_sii.index # the row index
numOfRows_s = df_net_income_sii.shape[0] #len(df_net_income_sii) #len(df_net_income_sii.index)
numOfColumns_s = df_net_income_sii.shape[1] #len(df_net_income_sii.columns)
headNameOfColumns_s = df_net_income_sii.columns

print(numOfColumns_s)
df_net_income_sii

for row_index_s in range(0, numOfRows_s):
    for col_index_s in range(0, numOfColumns_s):
        #print(df_net_income_sii.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_net_income_sii.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_net_income_sii.columns.values[col_index_s]): # if (df_net_income_sii.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_net_income_sii.columns.values[col_index_s]):
                continue
            elif (u"公司名稱" in df_net_income_sii.columns.values[col_index_s]):
                continue
            elif (col_index_s == numOfColumns_s-1):
                continue
            else:
                df_net_income_sii.iloc[row_index_s, col_index_s] = float(df_net_income_sii.iloc[row_index_s, col_index_s]) - float(df_net_income_sii.iloc[row_index_s, col_index_s+1])

df_net_income_sii              

In [16]:
df_net_income_otc = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'otc', 'NetIncome', '稅後純益率(%)(稅後純益)/(營業收入)', '營益分析彙總表')

df_net_income_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



稅後純益率(%)(稅後純益)/(營業收入)
year: 107
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 2


公司代號    公司名稱 NetIncome(%)_107Q2 NetIncome(%)_107Q1 NetIncome(%)_106Q4  \
0    1258   其祥-KY               1.19               1.74               2.45   
1    1259      安心               2.25               1.75               3.02   
2    1264      德麥              12.96              12.02              13.99   
3    1333     恩得利             -70.37             -66.59             -29.03   
4    1336      台翰               3.73               1.89               4.42   
5    1565    精華光學              25.14              22.29              24.76   
6    1566      捷邦               1.54               1.08               2.07   
7    1569      濱川               0.95               0.54               7.74   
8    1570    力肯實業              10.82               7.32               9.47   
9    1580    新麥企業               9.50               5.86              11.86   
10   1584    精剛精密             -12.73             -17.46              -8.36   
11   1586    和勤精機               4.57               2.51               1.36   
12   1591   駿吉-KY               3.79               0.18               0.45   
13   1593      祺驊              11.39               6.12              13.70   
14   1595    川寶科技               9.73               3.77              21.67   
15   1597      直得              23.00              19.68              15.98   
16   1599     宏佳騰               0.79              -3.16               6.07   
17   1742      台蠟             -32.71             -16.61               2.10   
18   1752      南光               8.82               9.97              12.36   
19   1777      生泰              21.94              13.57               8.60   
20   1781    合世生醫              -7.57             -19.04             -12.73   
21   1784    訊聯生技               6.33               9.35               0.24   
22   1785     光洋科               3.35               2.64               0.74   
23   1787     福盈科               6.15               5.36               7.45   
24   1788    杏昌生技               8.32               7.70               8.52   
25   1795    美時製藥              -0.76               1.68               0.76   
26   1799      易威             -75.97             -66.85             -87.46   
27   1813     寶利徠              16.09               2.66              -4.95   
28   1815    富喬工業              10.63              12.19              10.11   
29   2035    唐榮公司              -2.85              -3.91               1.29   
30   2061      風青               1.90               2.43               2.42   
31   2063      世鎧              15.09              15.14              12.51   
32   2064      晉椿               3.72               0.18               1.00   
33   2066      世德              15.10               3.08              12.76   
34   2067      嘉鋼               4.06               1.55              -3.70   
35   2221    大甲永和              13.44              11.72               9.66   
36   2230      泰茂               1.20              -7.42              -3.05   
37   2233      宇隆              16.79              10.79              16.58   
38   2235      謚源              13.06              10.75              13.66   
39   2596    綠意開發              35.35              38.10              28.57   
40   2640     大車隊              12.67              14.00              13.11   
41   2641    正德海運              10.95              16.10             -66.44   
42   2643      捷迅               2.14               1.79               2.14   
43   2718      晶悅              -7.22              -1.06               1.01   
44   2719     燦星旅              -3.56              -8.30              -4.89   
45   2724   富驛-KY             -13.22             -31.29             -32.44   
46   2726   雅茗-KY               5.26               6.46               7.67   
47   2729    瓦城泰統               8.88               8.58               7.99   
48   2732    六角國際               4.23               2.49               7.42   
49   2734     易飛網              -2.98               0.60              -6.48   
50   2736      高野          

In [ ]:
#Every single quarter data

#Each Dataframe object has a member variable shape i.e. a tuple that contains dimensions of a dataframe like,
#(Number_of_index, Number_of_columns)
#idx = df_net_income_otc.columns # the column index
#idx = df_net_income_otc.index # the row index
numOfRows_o = df_net_income_otc.shape[0] #len(df_net_income_otc) #len(df_net_income_otc.index)
numOfColumns_o = df_net_income_otc.shape[1] #len(df_net_income_otc.columns)
headNameOfColumns_o = df_net_income_otc.columns

print(numOfColumns_o)
df_net_income_otc

for row_index_o in range(0, numOfRows_o):
    for col_index_o in range(0, numOfColumns_o):
        #print(df_net_income_otc.columns.values[col_index].find('Q1')) # index of match string
        #print("Q1" in df_net_income_otc.columns.values[col_index]) # True OR False
        #How to Check if a Python String Contains Another String?
        if ("Q1" in df_net_income_otc.columns.values[col_index_o]): # if (df_net_income_otc.columns.values[col_index].find('Q1') > -1):
            continue
        else:
            if (u"公司代號" in df_net_income_otc.columns.values[col_index_o]):
                continue
            elif (u"公司名稱" in df_net_income_otc.columns.values[col_index_o]):
                continue
            elif (col_index_o == numOfColumns_o-1):
                continue
            else:
                df_net_income_otc.iloc[row_index_o, col_index_o] = float(df_net_income_otc.iloc[row_index_o, col_index_o]) - float(df_net_income_otc.iloc[row_index_o, col_index_o+1])

df_net_income_otc              

In [17]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_net_income = pd.concat([df_net_income_sii,df_net_income_otc],axis=0, ignore_index=True)

df_net_income

公司代號     公司名稱 NetIncome(%)_107Q2 NetIncome(%)_107Q1 NetIncome(%)_106Q4  \
0     1101       台泥              18.39              11.85              10.50   
1     1102       亞泥              19.95              14.57              10.27   
2     1103       嘉泥              44.12              33.99              46.64   
3     1104     環球水泥              17.64               0.20              31.54   
4     1108     幸福水泥              -0.48              -0.74              -3.00   
5     1109     信大水泥              13.96              16.05              13.21   
6     1110       東泥               7.00               3.72               3.40   
7     1201     味全公司              -0.58               3.27               5.03   
8     1203     味王公司              11.26              10.51              12.05   
9     1210     大成長城               3.73               5.40               3.49   
10    1213       大飲               0.69               1.13               0.31   
11    1215     卜蜂企業               4.02               5.44               7.44   
12    1216       統一               7.07               6.26              15.00   
13    1217      愛之味               0.42               3.90               3.50   
14    1218     泰山企業               5.61               4.40               4.13   
15    1219     福壽實業               1.03               1.56               0.51   
16    1220       台榮               5.51               5.89               3.56   
17    1225      福懋油               3.33               3.44               2.98   
18    1227       佳格               8.82              10.03               8.35   
19    1229     聯華實業              47.80              44.53              61.07   
20    1231     聯華食品               5.37               6.68               5.79   
21    1232      大統益               5.24               4.91               4.93   
22    1233       天仁               8.68               6.97               8.23   
23    1234       黑松               6.48               5.13               5.98   
24    1235       興泰             211.87             150.04             399.16   
25    1236     宏亞食品              -1.94               5.88               0.27   
26    1256  鮮活果汁-KY              13.58               9.32               9.84   
27    1262    綠悅-KY              -8.61              -1.83              12.16   
28    1301       台塑              24.89              21.94              23.89   
29    1303     南亞塑膠              17.71              16.14              17.63   
30    1304       台聚               5.50               5.56               4.66   
31    1305       華夏              12.81              14.08               9.11   
32    1307     三芳化工               3.68               4.33               9.14   
33    1308       亞聚               5.45               6.24               8.83   
34    1309     台達化工               3.54               3.92               2.53   
35    1310       台苯               8.84               9.66               6.67   
36    1312     國喬石化              14.98              15.74              14.76   
37    1313       聯成               1.93               3.18               4.63   
38    1314      中石化              12.25              11.62              18.26   
39    1315     達新工業              -1.47              -1.54               6.34   
40    1316       上曜              18.57              18.01              15.10   
41    1319       東陽               9.07               8.06               9.80   
42    1321       大洋              -1.38               3.34              -1.82   
43    1323       永裕               9.46               8.67               9.68   
44    1324     地球工業               0.19              -2.06               4.91   
45    1325       恒大               7.07               3.34               4.59   
46    1326       台化              15.38              14.48              16.75   
47    1337    再生-KY             -39.96             -39.92               3.97   
48    1338    廣華-KY               7.78               9.21               9.31   
49    

In [18]:
#檢查column資料型態

#df_net_income.info() #non-null object
#df_net_income.dtypes #object
#df_net_income.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
NetIncome(%)_107Q1    float64
NetIncome(%)_106Q4    float64
NetIncome(%)_106Q3    float64
NetIncome(%)_106Q2    float64
NetIncome(%)_106Q1    float64
NetIncome(%)_105Q4    float64
NetIncome(%)_105Q3    float64
NetIncome(%)_105Q2    float64
NetIncome(%)_105Q1    float64
NetIncome(%)_104Q4    float64
NetIncome(%)_104Q3    float64
NetIncome(%)_104Q2    float64
NetIncome(%)_104Q1    float64
dtype: object
'''

df_net_income = df_net_income.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_net_income.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                    int64
公司名稱                   object
NetIncome(%)_107Q2    float64
NetIncome(%)_107Q1    float64
NetIncome(%)_106Q4    float64
NetIncome(%)_106Q3    float64
NetIncome(%)_106Q2    float64
NetIncome(%)_106Q1    float64
NetIncome(%)_105Q4    float64
NetIncome(%)_105Q3    float64
NetIncome(%)_105Q2    float64
NetIncome(%)_105Q1    float64
NetIncome(%)_104Q4    float64
NetIncome(%)_104Q3    float64
NetIncome(%)_104Q2    float64
dtype: object

In [19]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [20]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['NetIncome(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['NetIncome(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['NetIncome(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [21]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['NetIncome(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [22]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_net_income['Growth_{0}Q{1}'.format(year, season)] = df_net_income.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [23]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_net_income['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_net_income.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [24]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [25]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True)#, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'有價證券代號及名稱'] != u'股票']
    df = df[~df[u'有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df[u'產業別'] > '0']
    del newdf[u'國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf[u'備註']

    df2=newdf[u'有價證券代號及名稱'].str.split(u' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if u'　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split(u'　')[1]
            df2.iat[i,0]=df2.iat[i,0].split(u'　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:u'公司代號',1:u'股票名稱'})
    del newdf[u'有價證券代號及名稱']

    return newdf

In [26]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_net_income = df_net_income.merge(df_basicinfo, on=u'公司代號', how='inner')

df_net_income

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  NetIncome(%)_107Q2  NetIncome(%)_107Q1  \
0     1101       台泥               18.39               11.85   
1     1102       亞泥               19.95               14.57   
2     1103       嘉泥               44.12               33.99   
3     1104     環球水泥               17.64                0.20   
4     1108     幸福水泥               -0.48               -0.74   
5     1109     信大水泥               13.96               16.05   
6     1110       東泥                7.00                3.72   
7     1201     味全公司               -0.58                3.27   
8     1203     味王公司               11.26               10.51   
9     1210     大成長城                3.73                5.40   
10    1213       大飲                0.69                1.13   
11    1215     卜蜂企業                4.02                5.44   
12    1216       統一                7.07                6.26   
13    1217      愛之味                0.42                3.90   
14    1218     泰山企業                5.61                4.40   
15    1219     福壽實業                1.03                1.56   
16    1220       台榮                5.51                5.89   
17    1225      福懋油                3.33                3.44   
18    1227       佳格                8.82               10.03   
19    1229     聯華實業               47.80               44.53   
20    1231     聯華食品                5.37                6.68   
21    1232      大統益                5.24                4.91   
22    1233       天仁                8.68                6.97   
23    1234       黑松                6.48                5.13   
24    1235       興泰              211.87              150.04   
25    1236     宏亞食品               -1.94                5.88   
26    1256  鮮活果汁-KY               13.58                9.32   
27    1262    綠悅-KY               -8.61               -1.83   
28    1301       台塑               24.89               21.94   
29    1303     南亞塑膠               17.71               16.14   
30    1304       台聚                5.50                5.56   
31    1305       華夏               12.81               14.08   
32    1307     三芳化工                3.68                4.33   
33    1308       亞聚                5.45                6.24   
34    1309     台達化工                3.54                3.92   
35    1310       台苯                8.84                9.66   
36    1312     國喬石化               14.98               15.74   
37    1313       聯成                1.93                3.18   
38    1314      中石化               12.25               11.62   
39    1315     達新工業               -1.47               -1.54   
40    1316       上曜               18.57               18.01   
41    1319       東陽                9.07                8.06   
42    1321       大洋               -1.38                3.34   
43    1323       永裕                9.46                8.67   
44    1324     地球工業                0.19               -2.06   
45    1325       恒大                7.07                3.34   
46    1326       台化               15.38               14.48   
47    1337    再生-KY              -39.96              -39.92   
48    1338    廣華-KY                7.78                9.21   
49    1339       昭輝               17.38                7.24   
50    1340    勝悅-KY               14.12               14.98   
51    1402      遠東新               10.26                7.97   
52    1410       南染               21.37               15.89   
53    1413     宏洲纖維                7.47                5.70   
54    1414       東和                3.09                2.09   
55    1416       廣豐               45.29              143.84   
56    1417       嘉裕              -11.16              -13.50   
57    1418       東華              -22.08              -38.89   
58    1419       新紡               -0.91              -16.74   
59    1423     利華羊毛               12.25                7.72   
60    1432    大魯閣實業              -31.45              -31.12   
61    1434     福懋興業                7.97                3.56   
62    1435     中福國際               38.

In [27]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_net_income.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_NetIncome.xlsx', 'NetIncome_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
